# Data Prepocessing

Dalam melakukan prepocessing dilakukan beberapa metode, berikut alur besar dari data prepocessing yang dilakukan
1. Data Cleaning
2. Case Folding
3. Stopwords
4. Steamming
5. Menghapus Data (Null dan Duplikat)

## Data Import Module dan Dataset dari Mongo DB
Data yang digunakan terlebih dahulu diambil dari raw datanya. Lalu akan di copy ke collection baru untuk dilakukan prepocessing.

In [1]:
import re
from pymongo import MongoClient
import pandas as pd
import nltk
from nltk.probability import FreqDist
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from Sastrawi.Stemmer.StemmerFactory import StemmerFactory
import string

In [2]:
# Membuat koneksi ke database MongoDB
client = MongoClient('localhost', 27017)
db = client['google_play_store_data'] 
raw_collection = db['01. raw_data_bibit']   
prepo_collection = db['02. prepo_data_bibit'] 

# Mengambil semua dokumen dari koleksi lama
data = raw_collection.find({}) 

# Menyimpan dokumen-dokumen tersebut ke dalam list
data_list = list(data)

# Menyimpan data ke dalam koleksi baru
prepo_collection.insert_many(data_list)


InsertManyResult([ObjectId('6638614cdd520c9ba22ee66c'), ObjectId('6638614cdd520c9ba22ee66d'), ObjectId('6638614cdd520c9ba22ee66e'), ObjectId('6638614cdd520c9ba22ee66f'), ObjectId('6638614cdd520c9ba22ee670'), ObjectId('6638614cdd520c9ba22ee671'), ObjectId('6638614cdd520c9ba22ee672'), ObjectId('6638614cdd520c9ba22ee673'), ObjectId('6638614cdd520c9ba22ee674'), ObjectId('6638614cdd520c9ba22ee675'), ObjectId('6638614cdd520c9ba22ee676'), ObjectId('6638614cdd520c9ba22ee677'), ObjectId('6638614cdd520c9ba22ee678'), ObjectId('6638614cdd520c9ba22ee679'), ObjectId('6638614cdd520c9ba22ee67a'), ObjectId('6638614cdd520c9ba22ee67b'), ObjectId('6638614cdd520c9ba22ee67c'), ObjectId('6638614cdd520c9ba22ee67d'), ObjectId('6638614cdd520c9ba22ee67e'), ObjectId('6638614cdd520c9ba22ee67f'), ObjectId('6638614cdd520c9ba22ee680'), ObjectId('6638614cdd520c9ba22ee681'), ObjectId('6638614cdd520c9ba22ee682'), ObjectId('6638614cdd520c9ba22ee683'), ObjectId('6638614cdd520c9ba22ee684'), ObjectId('6638614cdd520c9ba22ee6

In [3]:
# Menghapus field yang tidak diperlukan
prepo_collection.update_many({}, {'$unset': {'reviewId': '', 'userName': '', 'userImage': '', 'score': '',
                                       'thumbsUpCount': '', 'reviewCreatedVersion': '','replyContent': '',
                                       'repliedAt': '', 'appVersion': ''}})

# Menampilkan data setelah penghapusan field
cursor = prepo_collection.find()
for document in cursor:
    print(document)

{'_id': ObjectId('6638614cdd520c9ba22ee66c'), 'content': '😁 halloo, mia ni, 3344, w Mau daftar aj di persulit dari bulan April gagal melulu. Daftar pertama foto diri sama KTP ,status gagal. Perbaikan foto diri sama SIM A, kembali lagi gagal. Perbaikan kembali foto diri sama SIM A + KTP, kembali lagi gagal. Chat admin idak membantu jadi males.', 'at': datetime.datetime(2024, 5, 5, 10, 54, 32)}
{'_id': ObjectId('6638614cdd520c9ba22ee66d'), 'content': 'Aku ngerasa ini apps kyknya palsu deh, kyk binomo bukan naik malah turun drastis banget kalo lewat dari 500rb ke atas saldo saya kalau 100rb gk pernah tuh ada yang namanya turun uangnya mau pakai bibit kyknya gk lagi² deh bukanya untung malah buntung', 'at': datetime.datetime(2024, 5, 3, 17, 16, 43)}
{'_id': ObjectId('6638614cdd520c9ba22ee66e'), 'content': 'MAAF SEBELUMNYA SAYA KASIH TAU JANGAN INVEST TERLALU BANYAK DI BIBIT KETIKA PENCAIRAN SALDO GAK MASUK SAYA UDAH HAMPIR 2 MINGGU GA MASUK² PADAHAL LAGI BUTUH BANGT BUAT RUMAH SAKIT TAPI C

## Data Cleaning
Dalam melakukan data cleaning dilakukan beberapa sub proses yakni
1. Menghapus karakter Non ASCII
2. Menghapus tanda baca
3. Menghapus karakter angka
4. Menghapus karakter single
5. Menghapus karakter duplikat
6. Normalisasi Data

In [4]:
# Fungsi untuk menghitung setiap perubahannya
def count_changes(original_text, modified_text):
    count = sum(1 for i, j in zip(original_text, modified_text) if i != j)
    return count

### 1. Menghapus Karakter Non ASCII
Pada tahapan ini semua karakter Non ASCII akan di replace menjadi ? (secara default)

In [5]:
def remove_ascii(text):
    modified_text = text.encode('ascii', 'replace').decode('ascii')
    changes_count = count_changes(text, modified_text)
    return modified_text, changes_count

cursor = prepo_collection.find()

total_cleaned_count = 0

for document in cursor:
    review = document['content']
    cleaned_review, cleaned_count = remove_ascii(review)
    prepo_collection.update_one({'_id': document['_id']}, {'$set': {'content': cleaned_review}})
    total_cleaned_count += cleaned_count

print(f"Jumlah karakter non-ASCII yang dihapus: {total_cleaned_count}")


Jumlah karakter non-ASCII yang dihapus: 1842


### 2. Menghapus Tanda Baca
Dalam menghapus tanda caba menggunakan `string.punctuation`

Untuk tanda baca yang akan terhapus yakni *!"\#\$%\&'\(\)\*\+,\-\./:;<=>\?@\[\\\]\^_`\{\|\}\~*

In [6]:
def remove_punctuation(text):
    punctuation_pattern = r'[' + re.escape(string.punctuation) + ']'
    modified_text = re.sub(punctuation_pattern, '', text)
    changes_count = count_changes(text, modified_text)
    return modified_text, changes_count

documents = prepo_collection.find()

total_cleaned_count = 0

for document in documents:
    review = document['content']
    cleaned_review, cleaned_count = remove_punctuation(review)
    prepo_collection.update_one({'_id': document['_id']}, {'$set': {'content': cleaned_review}})
    total_cleaned_count += cleaned_count

print(f"Jumlah tanda baca yang dihapus: {total_cleaned_count}")


Jumlah tanda baca yang dihapus: 568684


### 3. Menghapus Karakter Angka
Semua karakter angka akan digantikan dengan spasi

In [7]:
def remove_number(text):
    modified_text = re.sub(r"\d+", " ", text)
    changes_count = count_changes(text, modified_text)
    return modified_text, changes_count

documents = prepo_collection.find()

total_cleaned_count = 0

for document in documents:
    review = document['content']
    cleaned_review, cleaned_count = remove_number(review)
    prepo_collection.update_one({'_id': document['_id']}, {'$set': {'content': cleaned_review}})
    total_cleaned_count += cleaned_count

print(f"Jumlah angka yang dihapus: {total_cleaned_count}")

Jumlah angka yang dihapus: 99361


### 4. Menghapus Karakter Single 
Karakter single yang dimaksud yakni karakter seperti 'a', 'y', 'i'

Karakter seperti itu tentunya tidak akan berguna untuk proses prediksi nantinya sehingga perlu dihapus

In [8]:
def remove_single_char(text):
    modified_text = re.sub(r"\b[a-zA-Z]\b", " ", text)
    changes_count = count_changes(text, modified_text)
    return modified_text, changes_count

documents = prepo_collection.find()

total_cleaned_count = 0

for document in documents:
    review = document['content']
    cleaned_review, cleaned_count = remove_single_char(review)
    prepo_collection.update_one({'_id': document['_id']}, {'$set': {'content': cleaned_review}})
    total_cleaned_count += cleaned_count

print(f"Jumlah karakter tunggal yang dihapus: {total_cleaned_count}")


Jumlah karakter tunggal yang dihapus: 933


### 5. Menghapus Karakter Duplikat 
Karakter duplikat yang dimaksud yakni seperti 'halooo', 'iyess'

Kata tersebut akan diganti menjadi 'halo' dan 'iyes'

In [9]:
def remove_duplicate_chars(text):
    words = text.split()
    cleaned_words = []
    changes_count = 0

    for word in words:
        cleaned_word = re.sub(r'(\w)\1+', r'\1', word)
        changes_count += count_changes(word, cleaned_word)
        cleaned_words.append(cleaned_word)
    
    cleaned_text = " ".join(cleaned_words)

    return cleaned_text, changes_count


cursor = prepo_collection.find()

total_changes_count = 0

for document in cursor:
    review = document['content']
    cleaned_review, changes_count = remove_duplicate_chars(review)
    prepo_collection.update_one(
        {'_id': document['_id']},
        {'$set': {'content': cleaned_review}}
    )
    total_changes_count += changes_count

print(f"Jumlah karakter ganda yang dihapus: {total_changes_count}")


Jumlah karakter ganda yang dihapus: 11610


### 6. Normalisasi Data
Normalisasi data adalah tahapan untuk mengganti kata-kata yang belum baku atau yang masih belum tepat berdasarkan kamus bahasa yang telah dibentuk sebelumnya.

Kamus bahasa berisi 2 kolom before dan after. Before untuk kata-kata yang belum baku/kurang tepat dan After untuk kata-kata yang benar


In [10]:
# Load data dari file Excel
df = pd.read_csv('kamus_normalisasi_baru.csv')

# Membuat dictionary dari data yang dibaca
abbreviations = dict(zip(df['before'], df['after']))

def count_changes(original_text, modified_text):
    count = sum(1 for i, j in zip(original_text, modified_text) if i != j)
    return count

def expand_abbreviations(text):
    tokens = text.split()
    # Untuk setiap word dalam tokens, ambil nilai dari abbreviations untuk kata tersebut jika ada, jika tidak, biarkan kata tersebut tetap seperti itu
    expanded_tokens = [abbreviations.get(word.lower(), word) for word in tokens]
    expanded_text = ' '.join(expanded_tokens)
    changes_count = count_changes(text, expanded_text)
    return expanded_text, changes_count


documents = prepo_collection.find()

total_expanded_count = 0

for document in documents:
    review = document['content']
    expanded_review, expanded_count = expand_abbreviations(review)
    prepo_collection.update_one({'_id': document['_id']}, {'$set': {'content': expanded_review}})
    total_expanded_count += expanded_count

print(f"Jumlah kata yang dinormalisasi: {total_expanded_count}")

Jumlah kata yang dinormalisasi: 549024


## Case Folding
Case Folding adalah proses pengubahan karakter teks menjadi huruf kecil (lowercase) atau huruf besar (uppercase) agar dapat diolah secara konsisten tanpa memperhatikan perbedaan besar kecilnya huruf.

In [11]:
def case_folding(text):
    lowercase_review = text.lower()
    changes_count = count_changes(text, lowercase_review)
    return lowercase_review, changes_count

cursor = prepo_collection.find()

total_changes_count = 0

for document in cursor:
    review = document['content']
    cleaned_review, changes_count = case_folding(review)
    prepo_collection.update_one(
        {'_id': document['_id']},
        {'$set': {'content': cleaned_review}}
    )

    total_changes_count += changes_count

# Menampilkan jumlah karakter ganda yang dihapus
print(f"Jumlah karakter yang dilakukan case folding: {total_changes_count}")

Jumlah karakter yang dilakukan case folding: 22593


## Melakukan Tokenisasi
Tokenisasi adalah proses memecah teks menjadi potongan-potongan kecil yang disebut dengan token. 

In [12]:
cursor = prepo_collection.find()

for document in cursor:
    review = document['content']
    tokens = word_tokenize(review)
    prepo_collection.update_one(
        {'_id': document['_id']},
        {'$set': {'tokenized_content': tokens}}
    )
    print(tokens)

['halo', 'mia', 'ni', 'mau', 'daftar', 'saja', 'di', 'persulit', 'dari', 'bulan', 'april', 'gagal', 'melulu', 'daftar', 'pertama', 'foto', 'diri', 'sama', 'ktp', 'status', 'gagal', 'perbaikan', 'foto', 'diri', 'sama', 'sim', 'kembali', 'lagi', 'gagal', 'perbaikan', 'kembali', 'foto', 'diri', 'sama', 'sim', 'ktp', 'kembali', 'lagi', 'gagal', 'tanya', 'admin', 'idak', 'membantu', 'jadi', 'males']
['aku', 'ngerasa', 'ini', 'aplikasi', 'sepertinya', 'palsu', 'sudah', 'seperti', 'binomo', 'bukan', 'naik', 'malah', 'turun', 'drastis', 'sangat', 'kalo', 'lewat', 'dari', 'ribu', 'ke', 'atas', 'saldo', 'saya', 'kalau', 'ribu', 'tidak', 'pernah', 'itu', 'ada', 'yang', 'namanya', 'turun', 'uangnya', 'mau', 'pakai', 'bibit', 'sepertinya', 'tidak', 'lagi', 'sudah', 'bukanya', 'untung', 'malah', 'buntung']
['maaf', 'sebelumnya', 'saya', 'kasih', 'tau', 'jangan', 'investasi', 'terlalu', 'banyak', 'di', 'bibit', 'ketika', 'pencairan', 'saldo', 'tidak', 'masuk', 'saya', 'sudah', 'hampir', 'minggu', 'ti

## Menghapus Stopwords
Stopwords adalah kata-kata umum yang sering muncul dalam teks namun kurang memiliki nilai informatif dalam pemrosesan teks. 

In [13]:
import nltk
from nltk.corpus import stopwords

cursor = prepo_collection.find()

# Mengambil daftar stopwords dalam bahasa Indonesia
list_stopwords = stopwords.words('indonesian')

list_stopwords.extend([
    "ny", 'um', 'klo', 'aah','ah','luu','we','wee','la','tah','kalo', 'biar', 'buat', 'bilang','bagaimana','cuma', 'karena', 'nya', 'nih', 'sih','at','gitu','tapi',
    'si', 'tau', 'tuh', 'untuk', 'ya', 'iya','mah','nder','jadi', 'sudah', 'saja','wah','ini','gw', 'hehe', 'pen','nan', 'loh', 'iii','wah','si','vi',
    'eee', 'setelah', 'tynyjunaz', 'ktol', 'yang', 'padahal', 'bagetikut', 'mu', 'loh', 'sih', 'tiba', 'tari', 'saja', 'ah',
    'kah', 'sekali', 'aju', 'hey', 'gini', 'halo', 'buk', 'si', 'hai', 'halo', 'min', 'lh', 'so', 'wae', 'jos', 'kalau', 'di', 'dh', 'dah',
    'ke', 'dom', 'juga', 'tiba', 'dari', 'ni', 'kak', 'mas', 'mba', 'eh', 'sat', 'ini', 'beuh', 'bat', 'rek', 'mingu'
])


In [14]:
list_stopwords = set(list_stopwords)

for document in cursor:
    review = document['tokenized_content']
    filtered_content = [word for word in review if word.lower() not in list_stopwords]
    
    # Memperbarui field 'filtered_review' dengan review yang sudah tidak mengandung stopwords
    prepo_collection.update_one(
        {'_id': document['_id']},
        {'$set': {'filtered_content': filtered_content}}
    )

    print (filtered_content)

['mia', 'daftar', 'persulit', 'april', 'gagal', 'melulu', 'daftar', 'foto', 'ktp', 'status', 'gagal', 'perbaikan', 'foto', 'sim', 'gagal', 'perbaikan', 'foto', 'sim', 'ktp', 'gagal', 'admin', 'idak', 'membantu', 'males']
['ngerasa', 'aplikasi', 'palsu', 'binomo', 'turun', 'drastis', 'ribu', 'saldo', 'ribu', 'namanya', 'turun', 'uangnya', 'pakai', 'bibit', 'bukanya', 'untung', 'buntung']
['maaf', 'kasih', 'investasi', 'bibit', 'pencairan', 'saldo', 'masuk', 'minggu', 'masuk', 'bangt', 'rumah', 'sakit', 'masuk', 'kecewa', 'berat', 'saldo', 'rekening', 'potong', 'sendoro', 'beli', 'motong', 'sendoro', 'bln', 'jjqngan', 'ple', 'bibit', 'anj', 'udah', 'dana', 'potong', 'unduh', 'aplikasi', 'motongin', 'uang', 'bln', 'aneh']
['sampah', 'jual', 'harga', 'tingi', 'verifikasi', 'penjualan', 'harga', 'kesokan', 'harinya']
['pencairan', 'ribu', 'jt', 'maksimal', 'kerja', 'lawak']
['ribet', 'mengunakan']
['verifikasi', 'akun', 'pengajuan', 'menghapus', 'akun', 'ikuti', 'prosedur', 'format', 'cs', 

## Stemming
Stemming adalah proses menghilangkan imbuhan (affixes) dari sebuah kata untuk menghasilkan bentuk dasarnya, yang disebut dengan "stem". Stemming bertujuan untuk mengembalikan kata-kata ke bentuk dasarnya agar kata-kata yang memiliki akar kata yang sama dapat dihitung sebagai satu kata dalam analisis teks.

In [15]:
# Inisialisasi objek stemmer
factory = StemmerFactory()
stemmer = factory.create_stemmer()

cursor = prepo_collection.find()

for document in cursor:
    filtered_content = document['filtered_content']
    
    # Melakukan stemming pada setiap kata dalam filtered_review
    stemmed_content = [stemmer.stem(word) for word in filtered_content]
    
    # Memperbarui field 'stemmed_review' dengan hasil stemming
    prepo_collection.update_one(
        {'_id': document['_id']},
        {'$set': {'stemmed_review': stemmed_content}}
    )

    print (stemmed_content)

['mia', 'daftar', 'sulit', 'april', 'gagal', 'melulu', 'daftar', 'foto', 'ktp', 'status', 'gagal', 'baik', 'foto', 'sim', 'gagal', 'baik', 'foto', 'sim', 'ktp', 'gagal', 'admin', 'idak', 'bantu', 'males']
['ngerasa', 'aplikasi', 'palsu', 'binomo', 'turun', 'drastis', 'ribu', 'saldo', 'ribu', 'nama', 'turun', 'uang', 'pakai', 'bibit', 'buka', 'untung', 'buntung']
['maaf', 'kasih', 'investasi', 'bibit', 'cair', 'saldo', 'masuk', 'minggu', 'masuk', 'bangt', 'rumah', 'sakit', 'masuk', 'kecewa', 'berat', 'saldo', 'rekening', 'potong', 'ndoro', 'beli', 'motong', 'ndoro', 'bln', 'jjqngan', 'ple', 'bibit', 'anj', 'udah', 'dana', 'potong', 'unduh', 'aplikasi', 'motongin', 'uang', 'bln', 'aneh']
['sampah', 'jual', 'harga', 'tingi', 'verifikasi', 'jual', 'harga', 'sok', 'hari']
['cair', 'ribu', 'jt', 'maksimal', 'kerja', 'lawak']
['ribet', 'mengunakan']
['verifikasi', 'akun', 'aju', 'hapus', 'akun', 'ikut', 'prosedur', 'format', 'cs', 'lihat', 'yakak', 'ulang', 'progres']
['verifikasi', 'minggu',

In [16]:
cursor = prepo_collection.find()

for document in cursor:
    stemmed_review = document['stemmed_review']
    
    # Mengubah array kata hasil stemming menjadi string
    data_clean = ' '.join(stemmed_review)
    
    # Memperbarui field 'data_clean' dengan hasil yang sudah diubah
    prepo_collection.update_one(
        {'_id': document['_id']},
        {'$set': {'data_clean': data_clean}}
    )

    print (data_clean)

mia daftar sulit april gagal melulu daftar foto ktp status gagal baik foto sim gagal baik foto sim ktp gagal admin idak bantu males
ngerasa aplikasi palsu binomo turun drastis ribu saldo ribu nama turun uang pakai bibit buka untung buntung
maaf kasih investasi bibit cair saldo masuk minggu masuk bangt rumah sakit masuk kecewa berat saldo rekening potong ndoro beli motong ndoro bln jjqngan ple bibit anj udah dana potong unduh aplikasi motongin uang bln aneh
sampah jual harga tingi verifikasi jual harga sok hari
cair ribu jt maksimal kerja lawak
ribet mengunakan
verifikasi akun aju hapus akun ikut prosedur format cs lihat yakak ulang progres
verifikasi minggu ac ac kecewa
bank jago akun susah
aplikasi bagus catat riwayat hasil jual aset jual laku dana mutasi rekening
pemeliharan rdn walet bosok isi cocok lihat kg nongol nongol saldo lelah
proses beli ribet makan hal proses cair
baharu suka masuk habis
biometrik masuk masukin sidik jari suruh masuk
loading buka aplikasi
investasi susah lo

## Menghapus Data Null dan Duplikat
Penghapusan ini dilakukan karena setelah melakukan proses diatas cukup banyak kolom `content` yang tidak memiliki data sehingga perlu di hapus.

Selain itu, terdapat juga kata-kata duplikat yang muncul seperti kata 'mantap' yang mana kata tersebut muncul di 200 baris sehingga perlu dihapus karena ingin mendapatkan data yang unik

In [17]:
# Mengecek dan menghapus dokumen dengan field "data_clean" yang kosong
query = {'data_clean': {'$exists': True, '$eq': ''}}
result = prepo_collection.delete_many(query)
print(f"Jumlah dokumen yang dihapus: {result.deleted_count}")

Jumlah dokumen yang dihapus: 209


In [18]:
# Pipeline untuk menghilangkan data duplikat berdasarkan field "data_clean"
pipeline = [
    {
        '$group': {
            '_id': '$data_clean',
            'uniqueIds': {'$addToSet': '$_id'},
            'count': {'$sum': 1}
        }
    },
    {
        '$match': {
            'count': {'$gt': 1}
        }
    }
]

# Eksekusi pipeline
duplicates = list(prepo_collection.aggregate(pipeline))

# Menghapus data duplikat
total_duplicates_removed = 0
for duplicate in duplicates:
    review_ids_to_remove = duplicate['uniqueIds'][1:]
    result = prepo_collection.delete_many({'_id': {'$in': review_ids_to_remove}})
    duplicates_removed_count = result.deleted_count
    total_duplicates_removed += duplicates_removed_count

print('Jumlah data duplikat yang dihapus:', total_duplicates_removed)


Jumlah data duplikat yang dihapus: 1287


In [19]:
# Data yang sudah bersih
cursor = prepo_collection.find()
df_bibit= pd.DataFrame(list(cursor))
df_bibit

_id  \
0     6638614cdd520c9ba22ee66c   
1     6638614cdd520c9ba22ee66d   
2     6638614cdd520c9ba22ee66e   
3     6638614cdd520c9ba22ee66f   
4     6638614cdd520c9ba22ee670   
...                        ...   
8230  663864e9dd520c9ba22f284a   
8231  663864e9dd520c9ba22f284b   
8232  663864e9dd520c9ba22f284c   
8233  663864e9dd520c9ba22f284d   
8234  663864e9dd520c9ba22f284e   

                                                content                  at  \
0     halo mia ni mau daftar saja di persulit dari b... 2024-05-05 10:54:32   
1     aku ngerasa ini aplikasi sepertinya palsu suda... 2024-05-03 17:16:43   
2     maaf sebelumnya saya kasih tau jangan investas... 2024-05-03 09:09:22   
3     sampah sudah jual di harga tingi tapi karena a... 2024-05-03 07:50:00   
4     pencairan ribu saja seperti jt maksimal hari k... 2024-05-02 11:55:53   
...                                                 ...                 ...   
8230  aku suka ini aplikasi next adain beli emas don... 2021-06-12 08:12:17   
8231  aplikasi yang banyak manfatnya terutama yang s... 2020-12-31 17:43:10   
8232  salah satu aplikasi aperd yang layak dintal da... 2021-04-06 22:11:23   
8233  saat daftar masukan kode referal fareltolemba ... 2023-01-01 15:18:20   
8234  sumpah saya suka sangat sama ini aplikasi cuku... 2021-06-20 18:26:03   

                                       tokenized_review  \
0     [halo, mia, ni, mau, daftar, saja, di, persuli...   
1     [aku, ngerasa, ini, aplikasi, sepertinya, pals...   
2     [maaf, sebelumnya, saya, kasih, tau, jangan, i...   
3     [sampah, sudah, jual, di, harga, tingi, tapi, ...   
4     [pencairan, ribu, saja, seperti, jt, maksimal,...   
...                                                 ...   
8230  [aku, suka, ini, aplikasi, next, adain, beli, ...   
8231  [aplikasi, yang, banyak, manfatnya, terutama, ...   
8232  [salah, satu, aplikasi, aperd, yang, layak, di...   
8233  [saat, daftar, masukan, kode, referal, farelto...   
8234  [sumpah, saya, suka, sangat, sama, ini, aplika...   

                                        filtered_review  \
0     [mia, daftar, persulit, april, gagal, melulu, ...   
1     [ngerasa, aplikasi, palsu, binomo, turun, dras...   
2     [maaf, kasih, investasi, bibit, pencairan, sal...   
3     [sampah, jual, harga, tingi, verifikasi, penju...   
4         [pencairan, ribu, jt, maksimal, kerja, lawak]   
...                                                 ...   
8230  [suka, aplikasi, next, adain, beli, emas, dola...   
8231  [aplikasi, manfatnya, khilaf, belanja, keuanga...   
8232  [salah, aplikasi, aperd, layak, dintal, berinv...   
8233  [daftar, masukan, kode, referal, fareltolemba,...   
8234  [sumpah, suka, aplikasi, bintang, berbicara, k...   

                                         stemmed_review  \
0     [mia, daftar, sulit, april, gagal, melulu, daf...   
1     [ngerasa, aplikasi, palsu, binomo, turun, dras...   
2     [maaf, kasih, investasi, bibit, cair, saldo, m...   
3     [sampah, jual, harga, tingi, verifikasi, jual,...   
4              [cair, ribu, jt, maksimal, kerja, lawak]   
...                                                 ...   
8230  [suka, aplikasi, next, adain, beli, emas, dola...   
8231  [aplikasi, manfatnya, khilaf, belanja, uang, r...   
8232  [salah, aplikasi, aperd, layak, dintal, invest...   
8233  [daftar, masuk, kode, referal, fareltolemba, l...   
8234  [sumpah, suka, aplikasi, bintang, bicara, kend...   

                                             data_clean  
0     mia daftar sulit april gagal melulu daftar fot...  
1     ngerasa aplikasi palsu binomo turun drastis ri...  
2     maaf kasih investasi bibit cair saldo masuk mi...  
3     sampah jual harga tingi verifikasi jual harga ...  
4                     cair ribu jt maksimal kerja lawak  
...                                                 ...  
8230  suka aplikasi next adain beli emas dolar index...  
8231  aplikasi manfatnya khilaf belanja uang rencana...  
8232  salah aplikasi

## Menyimpan Data Clean pada Collection Baru

In [21]:
client = MongoClient('localhost', 27017)
db = client['google_play_store_data'] 
prepo_collection = db['02. prepo_data_bibit']  
clean_collection = db['03. clean_data_bibit'] 

# Mengambil beberapa dokumen dari prepo_collection
data = prepo_collection.find({}) 

# Menyimpan dokumen-dokumen tersebut ke dalam list
data_list = list(data)

# Menyimpan data ke dalam clean_collection
clean_collection.insert_many(data_list)


InsertManyResult([ObjectId('6638614cdd520c9ba22ee66c'), ObjectId('6638614cdd520c9ba22ee66d'), ObjectId('6638614cdd520c9ba22ee66e'), ObjectId('6638614cdd520c9ba22ee66f'), ObjectId('6638614cdd520c9ba22ee670'), ObjectId('6638614cdd520c9ba22ee671'), ObjectId('6638614cdd520c9ba22ee672'), ObjectId('6638614cdd520c9ba22ee673'), ObjectId('6638614cdd520c9ba22ee674'), ObjectId('6638614cdd520c9ba22ee675'), ObjectId('6638614cdd520c9ba22ee676'), ObjectId('6638614cdd520c9ba22ee677'), ObjectId('6638614cdd520c9ba22ee678'), ObjectId('6638614cdd520c9ba22ee679'), ObjectId('6638614cdd520c9ba22ee67a'), ObjectId('6638614cdd520c9ba22ee67b'), ObjectId('6638614cdd520c9ba22ee67c'), ObjectId('6638614cdd520c9ba22ee67d'), ObjectId('6638614cdd520c9ba22ee67e'), ObjectId('6638614cdd520c9ba22ee67f'), ObjectId('6638614cdd520c9ba22ee680'), ObjectId('6638614cdd520c9ba22ee681'), ObjectId('6638614cdd520c9ba22ee682'), ObjectId('6638614cdd520c9ba22ee683'), ObjectId('6638614cdd520c9ba22ee684'), ObjectId('6638614cdd520c9ba22ee6

In [22]:
# Menghapus field yang tidak diperlukan
clean_collection.update_many({}, {'$unset': {'tokenized_content': '', 'filtered_content': '', 'stemmed_review': '', 'content': ''}})

# Menampilkan data setelah penghapusan field
cursor = clean_collection.find()
for document in cursor:
    print(document)

{'_id': ObjectId('6638614cdd520c9ba22ee66c'), 'at': datetime.datetime(2024, 5, 5, 10, 54, 32), 'data_clean': 'mia daftar sulit april gagal melulu daftar foto ktp status gagal baik foto sim gagal baik foto sim ktp gagal admin idak bantu males'}
{'_id': ObjectId('6638614cdd520c9ba22ee66d'), 'at': datetime.datetime(2024, 5, 3, 17, 16, 43), 'data_clean': 'ngerasa aplikasi palsu binomo turun drastis ribu saldo ribu nama turun uang pakai bibit buka untung buntung'}
{'_id': ObjectId('6638614cdd520c9ba22ee66e'), 'at': datetime.datetime(2024, 5, 3, 9, 9, 22), 'data_clean': 'maaf kasih investasi bibit cair saldo masuk minggu masuk bangt rumah sakit masuk kecewa berat saldo rekening potong ndoro beli motong ndoro bln jjqngan ple bibit anj udah dana potong unduh aplikasi motongin uang bln aneh'}
{'_id': ObjectId('6638614cdd520c9ba22ee66f'), 'at': datetime.datetime(2024, 5, 3, 7, 50), 'data_clean': 'sampah jual harga tingi verifikasi jual harga sok hari'}
{'_id': ObjectId('6638614cdd520c9ba22ee670'

In [23]:
# Menambahkan kolom label dengan nilai default None
clean_collection.update_many(
    {},
    {
        '$set': {
            'label': None
        }
    }
)

UpdateResult({'n': 8235, 'nModified': 8235, 'ok': 1.0, 'updatedExisting': True}, acknowledged=True)

In [24]:
client.close()